In [ ]:
"""
>Feature gb|AE005674.2|
190	255	gene
			gene	thrL
			locus_tag	SF0001
190	255	CDS
			product	thr operon leader peptide
			transl_table	11
			protein_id	gb|AAN41668.1||gnl|mgcchina|SF0000001
336	2798	gene
			gene	thrA
			locus_tag	SF0002
336	2798	CDS
			product	aspartokinase I, homoserine dehydrogenase I
			transl_table	11
			protein_id	gb|AAN41669.2||gnl|mgcchina|SF0000002

CDSs [CDS1, CDS2, ...]
    CDS = [min_coord, max_coord, ori, pseudo, protein_id,  product]
        ori in (+1,-1)
"""

# parameters

import sys
import optparse

if len(sys.argv) == 1:

    print ("Reformat features downloaded from NCBI nucleotide DB into")
    print (".tsv table of CDSs")
    print (" -h for help on parameters")
    exit()
                                                                    
parser = optparse.OptionParser()
parser.add_option("-i", "--infile",  help = "infile in NCBI nucleotides sequence,\
                                     send to file Feature table format,\
                                     default = sequence.txt", 
                                     default = "sequence.txt")
parser.add_option("-o", "--outfile", help = "outfile with all CDSs,\
                                     default = CDSs.tsv",\
                                     default ="CDSs.tsv")
option, args = parser.parse_args()
    
infile  = option.infile
outfile = option.outfile

recognized = {"protein_id":5, "pseudo":4, "product":6}
CDS_fields = ["#min_coord", "max_coord", "ori", "locus_tag", "pseudo", "protein_id",  "product"]

##### main 
f = open(infile)
CDSclosed = True
geneclosed = True
locus_tag = ""
CDSs = []
print ("wait..")
for line in f:
    if len(line.strip())== 0:
        continue
    line_ = line.split()    
    if (len(line_)) == 3:
# New gene
        if line_[0].isdigit() and line_[1].isdigit() and line_[2] == "gene":
            geneclosed = False
            CDSclosed = True
            locus_tag = ""
            continue
        if line_[0].isdigit() and line_[1].isdigit() and line_[2] == "CDS":
# New CDS
            min_coord = min(int(line_[0]), int(line_[1]))
            max_coord = max(int(line_[0]),int(line_[1]))
            if int(line_[0]) > int(line_[1]) :
                ori = -1
            else:
                ori = +1
            CDSs.append([min_coord, max_coord, ori, locus_tag,"","",""])
            CDSclosed = False
            CDSattributes = {}
            geneclosed = True
            continue
# attributes <=>  0 < len(line_) <> 3 
    attribute_ = line.strip().split(None,1)
    att_name = attribute_[0]
#    print(att_name)
    if att_name == "locus_tag":
        locus_tag = attribute_[1]
    if len(attribute_) == 1:
        att_value = "yes"
    else:
        att_value = attribute_[1]
    if att_name not in recognized:
        continue
# Add attribute value to CDS
    CDSs[-1][recognized[att_name]] += att_value.strip()
    continue
f.close()
print ("%s CDSs stored" % len(CDSs) )

g = open(outfile, 'w')
title = "\t".join(CDS_fields) 
g.write (title + "\n")

# write CDSs             
for CDS in CDSs:
    for field in CDS:
        g.write("%s\t" % field)
    g.write("\n")
print ("..done")